# Importing the Libraries

In [1]:
import pandas as pd
import os
import numpy as np
import datetime
import math

import pandas_profiling 
from sklearn.preprocessing import LabelEncoder


import matplotlib.pyplot as plt
%matplotlib inline

import missingno as msno
import seaborn as sns


from sklearn.linear_model import LinearRegression,LogisticRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import RandomForestRegressor


# Import Bokeh
from bokeh.plotting import figure, output_file, show
from bokeh.palettes import d3
from bokeh.io import output_notebook
from bokeh.models import Legend

from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score

output_notebook()

Loading BokehJS ...

# EDA on Training and Testing data

In [2]:
DATA_DIR = "./dataset/"

train_data = os.path.join(DATA_DIR,"train.csv")
test_data = os.path.join(DATA_DIR,"test.csv")


train_data_ini = os.path.join(DATA_DIR,"train.csv")
test_data_ini = os.path.join(DATA_DIR,"test.csv")

In [3]:
train_data = pd.read_csv(train_data)
test_data = pd.read_csv(test_data)


In [4]:

test_data_ini = pd.read_csv(test_data_ini)

In [5]:
print("Number of rows ",train_data.shape[0])
print("Number of columns ",train_data.shape[1])

Number of rows  6500
Number of columns  20


In [6]:
print("Number of rows ",test_data.shape[0])
print("Number of columns ",test_data.shape[1])

Number of rows  3500
Number of columns  19


In [7]:
train_data.head()

Customer Id     Artist Name  Artist Reputation  Height  Width  \
0  fffe3900350033003300   Billy Jenkins               0.26    17.0    6.0   
1  fffe3800330031003900     Jean Bryant               0.28     3.0    3.0   
2  fffe3600370035003100    Laura Miller               0.07     8.0    5.0   
3      fffe350031003300  Robert Chaires               0.12     9.0    NaN   
4  fffe3900320038003400    Rosalyn Krol               0.15    17.0    6.0   

   Weight   Material  Price Of Sculpture  Base Shipping Price International  \
0  4128.0      Brass               13.91                16.27           Yes   
1    61.0      Brass                6.83                15.00            No   
2   237.0       Clay                4.96                21.18            No   
3     NaN  Aluminium                5.81                16.31            No   
4   324.0  Aluminium                3.18                11.94           Yes   

  Express Shipment Installation Included Transport Fragile  \
0              Yes                    No   Airways      No   
1               No                    No  Roadways      No   
2               No                    No  Roadways     Yes   
3               No                    No       NaN      No   
4              Yes                   Yes   Airways      No   

  Customer Information Remote Location Scheduled Date Delivery Date  \
0        Working Class              No       06/07/15      06/03/15   
1        Working Class              No       03/06/17      03/05/17   
2        Working Class             Yes       03/09/15      03/08/15   
3              Wealthy             Yes       05/24/15      05/20/15   
4        Working Class              No       12/18/16      12/14/16   

           Customer Location    Cost  
0     New Michelle, OH 50777 -283.29  
1  New Michaelport, WY 12072 -159.96  
2      Bowmanshire, WA 19241 -154.29  
3       East Robyn, KY 86375 -161.16  
4        Aprilside, PA 52793 -159.23

In [8]:
train_data.profile_report()

In [9]:
test_data.profile_report()

In [10]:
train_data.isnull().sum()

Customer Id                 0
Artist Name                 0
Artist Reputation         750
Height                    375
Width                     584
Weight                    587
Material                  764
Price Of Sculpture          0
Base Shipping Price         0
International               0
Express Shipment            0
Installation Included       0
Transport                1392
Fragile                     0
Customer Information        0
Remote Location           771
Scheduled Date              0
Delivery Date               0
Customer Location           0
Cost                        0
dtype: int64

# Filling NaN or Null Values 

In [11]:
train_data['Artist Reputation'].fillna(train_data['Artist Reputation'].mean(),inplace=True)
train_data['Height'].fillna(train_data['Height'].mean(),inplace=True)
train_data['Width'].fillna(train_data['Width'].mean(),inplace=True)
train_data['Weight'].fillna(train_data['Weight'].mean(),inplace=True)

train_data['Material'].fillna(train_data['Material'].mode()[0],inplace=True)
train_data['Transport'].fillna(train_data['Transport'].mode()[0],inplace=True)
train_data['Remote Location'].fillna(train_data['Remote Location'].mode()[0],inplace=True)



In [12]:
test_data['Artist Reputation'].fillna(test_data['Artist Reputation'].mean(),inplace=True)
test_data['Height'].fillna(test_data['Height'].mean(),inplace=True)
test_data['Width'].fillna(test_data['Width'].mean(),inplace=True)
test_data['Weight'].fillna(test_data['Weight'].mean(),inplace=True)

test_data['Material'].fillna(test_data['Material'].mode()[0],inplace=True)
test_data['Transport'].fillna(test_data['Transport'].mode()[0],inplace=True)
test_data['Remote Location'].fillna(test_data['Remote Location'].mode()[0],inplace=True)



# Feature Engineering

In [13]:
train_data['Area'] = train_data.apply(lambda x:x['Height']*x['Width'],axis=1)
train_data['Combined_Price'] = train_data.apply(lambda x:x['Price Of Sculpture']+x['Base Shipping Price'],axis=1)

In [14]:
test_data['Area'] = test_data.apply(lambda x:x['Height']*x['Width'],axis=1)
test_data['Combined_Price'] = test_data.apply(lambda x:x['Price Of Sculpture']+x['Base Shipping Price'],axis=1)

In [15]:
train_data['Cost'] = train_data['Cost'].apply(lambda x:abs(x))

# test_data['Cost'] = test_data['Cost'].apply(lambda x:abs(x)) as no cost in test_data

In [16]:
unique_artist_name = list(set(train_data['Artist Name'].tolist()))

print(len(unique_artist_name))
print(train_data.shape[0]) 

6449
6500


In [17]:
train_data['Material'].value_counts()

Brass        1611
Aluminium     845
Bronze        821
Marble        819
Clay          816
Wood          816
Stone         772
Name: Material, dtype: int64

In [18]:
len(train_data['Customer Location'].value_counts())

6500

In [19]:
datetimeFormat = '%m/%d/%y'
def fun(a,b):
    diff = datetime.datetime.strptime(b, datetimeFormat)-datetime.datetime.strptime(a, datetimeFormat)
#     print(diff.seconds)
#     print(diff.total_seconds()/3600)
    return(diff.total_seconds()/3600.0)

# fun("06/07/15","06/03/15")
train_data['shipping_time_in_hrs'] = train_data.apply(lambda x:fun(x['Scheduled Date'],x['Delivery Date']),axis=1) 
test_data['shipping_time_in_hrs'] = test_data.apply(lambda x:fun(x['Scheduled Date'],x['Delivery Date']),axis=1) 
    

In [20]:
train_data.drop(columns = ['Customer Id','Artist Name','Height','Width','Price Of Sculpture','Base Shipping Price','Scheduled Date','Delivery Date','Customer Location'],axis=1,inplace=True)

test_data.drop(columns = ['Customer Id','Artist Name','Height','Width','Price Of Sculpture','Base Shipping Price','Scheduled Date','Delivery Date','Customer Location'],axis=1,inplace=True)

In [21]:
train_data.head()

Artist Reputation         Weight   Material International Express Shipment  \
0               0.26    4128.000000      Brass           Yes              Yes   
1               0.28      61.000000      Brass            No               No   
2               0.07     237.000000       Clay            No               No   
3               0.12  400694.821918  Aluminium            No               No   
4               0.15     324.000000  Aluminium           Yes              Yes   

  Installation Included Transport Fragile Customer Information  \
0                    No   Airways      No        Working Class   
1                    No  Roadways      No        Working Class   
2                    No  Roadways     Yes        Working Class   
3                    No  Roadways      No              Wealthy   
4                   Yes   Airways      No        Working Class   

  Remote Location    Cost        Area  Combined_Price  shipping_time_in_hrs  
0              No  283.29  102.000000           30.18                 -96.0  
1              No  159.96    9.000000           21.83                 -24.0  
2             Yes  154.29   40.000000           26.14                 -24.0  
3             Yes  161.16   86.558824           22.12                 -96.0  
4              No  159.23  102.000000           15.12                 -96.0

# Label Encoding 
 
Converting the categorical object columns to equivalent numerical values

In [22]:
lab_en = LabelEncoder()
train_data.loc[:,'Material'] = lab_en.fit_transform(train_data.loc[:,'Material'])
train_data.loc[:,'International'] = lab_en.fit_transform(train_data.loc[:,'International'])
train_data.loc[:,'Express Shipment'] = lab_en.fit_transform(train_data.loc[:,'Express Shipment'])
train_data.loc[:,'Installation Included'] = lab_en.fit_transform(train_data.loc[:,'Installation Included'])
train_data.loc[:,'Transport'] = lab_en.fit_transform(train_data.loc[:,'Transport'])
train_data.loc[:,'Fragile'] = lab_en.fit_transform(train_data.loc[:,'Fragile'])
train_data.loc[:,'Customer Information'] = lab_en.fit_transform(train_data.loc[:,'Customer Information'])
train_data.loc[:,'Remote Location'] = lab_en.fit_transform(train_data.loc[:,'Remote Location'])


test_data.loc[:,'Material'] = lab_en.fit_transform(test_data.loc[:,'Material'])
test_data.loc[:,'International'] = lab_en.fit_transform(test_data.loc[:,'International'])
test_data.loc[:,'Express Shipment'] = lab_en.fit_transform(test_data.loc[:,'Express Shipment'])
test_data.loc[:,'Installation Included'] = lab_en.fit_transform(test_data.loc[:,'Installation Included'])
test_data.loc[:,'Transport'] = lab_en.fit_transform(test_data.loc[:,'Transport'])
test_data.loc[:,'Fragile'] = lab_en.fit_transform(test_data.loc[:,'Fragile'])
test_data.loc[:,'Customer Information'] = lab_en.fit_transform(test_data.loc[:,'Customer Information'])
test_data.loc[:,'Remote Location'] = lab_en.fit_transform(test_data.loc[:,'Remote Location'])


In [23]:

X_train = train_data.loc[:,train_data.columns!="Cost"]
Y_train = train_data.loc[:,train_data.columns=='Cost']

In [24]:
X_train.head()

Artist Reputation         Weight  Material  International  \
0               0.26    4128.000000         1              1   
1               0.28      61.000000         1              0   
2               0.07     237.000000         3              0   
3               0.12  400694.821918         0              0   
4               0.15     324.000000         0              1   

   Express Shipment  Installation Included  Transport  Fragile  \
0                 1                      0          0        0   
1                 0                      0          1        0   
2                 0                      0          1        1   
3                 0                      0          1        0   
4                 1                      1          0        0   

   Customer Information  Remote Location        Area  Combined_Price  \
0                     1                0  102.000000           30.18   
1                     1                0    9.000000           21.83   
2                     1                1   40.000000           26.14   
3                     0                1   86.558824           22.12   
4                     1                0  102.000000           15.12   

   shipping_time_in_hrs  
0                 -96.0  
1                 -24.0  
2                 -24.0  
3                 -96.0  
4                 -96.0

In [25]:
Y_train.head()

Cost
0  283.29
1  159.96
2  154.29
3  161.16
4  159.23

# Normalizing the data

In [26]:

columns = ['Weight','Area','Combined_Price','shipping_time_in_hrs']

def normalize(df,columns_list):
    result = df.copy()
    for feature_name in columns_list:
        max_value = df[feature_name].max()
        min_value = df[feature_name].min()
        result[feature_name] = np.round((df[feature_name] - df[feature_name].mean()) / df[feature_name].std(),3)
    return result

X_train1 = normalize(X_train,columns)
X_test1 = test_data
X_test1 = normalize(X_test1,columns)

# Training the Model

In [27]:

rf = RandomForestRegressor(n_estimators=100,max_depth=10,random_state=42)
rf.fit(X_train1, Y_train.values.ravel())
# Y_predict = rf.predict(X_test1)

<ipython-input-27-df837b84823c>:2: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  rf.fit(X_train1, Y_train)


RandomForestRegressor(max_depth=10, random_state=42)

# Generating Prediction Results

In [28]:
data_submit = pd.DataFrame()

data_submit.loc[:,'Customer Id'] = test_data_ini.loc[:,'Customer Id']
data_submit['Cost'] = Y_predict
data_submit['Cost'] = data_submit['Cost'].abs()

In [29]:
data_submit.to_csv("submission1.csv",index=False)

![](./images/results_submission2.png)

# Hyperparameter Tuning

For better results

In [30]:

from sklearn.model_selection import RandomizedSearchCV

param_grid = [
{'n_estimators': [50,100,250,500], 
 'max_depth': [10, 50, 100], 'bootstrap': [True, False]}
]

rf_random = RandomizedSearchCV(rf, param_grid, cv=10,verbose=10)
rf_random.fit(X_train,Y_train.values.ravel())

tuned_rf_best = rf_random.best_estimator_

Y_predict = tuned_rf_best.predict(X_test1)


Fitting 10 folds for each of 10 candidates, totalling 100 fits
[CV] n_estimators=500, max_depth=10, bootstrap=False .................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV]  n_estimators=500, max_depth=10, bootstrap=False, score=-0.396, total=  13.0s
[CV] n_estimators=500, max_depth=10, bootstrap=False .................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   13.0s remaining:    0.0s


[CV]  n_estimators=500, max_depth=10, bootstrap=False, score=-1.755, total=  12.9s
[CV] n_estimators=500, max_depth=10, bootstrap=False .................


...

[CV]  n_estimators=500, max_depth=10, bootstrap=False, score=-0.374, total=  14.2s
[CV] n_estimators=500, max_depth=10, bootstrap=False .................


[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:  2.0min remaining:    0.0s


[CV]  n_estimators=500, max_depth=10, bootstrap=False, score=-7.296, total=  12.9s
[CV] n_estimators=100, max_depth=100, bootstrap=True .................
[CV]  n_estimators=100, max_depth=100, bootstrap=True, score=-0.887, total=   3.5s
[CV] n_estimators=100, max_depth=100, bootstrap=True .................
[CV]  n_estimators=100, max_depth=100, bootstrap=True, score=0.070, total=   3.4s
[CV] n_estimators=100, max_depth=100, bootstrap=True .................
[CV]  n_estimators=100, max_depth=100, bootstrap=True, score=-0.636, total=   3.4s
[CV] n_estimators=100, max_depth=100, bootstrap=True .................
[CV]  n_estimators=100, max_depth=100, bootstrap=True, score=-0.800, total=   3.2s
[CV] n_estimators=100, max_depth=100, bootstrap=True .................
[CV]  n_estimators=100, max_depth=100, bootstrap=True, score=0.677, total=   3.2s
[CV] n_estimators=100, max_depth=100, bootstrap=True .................
[CV]  n_estimators=100, max_depth=100, bootstrap=True, score=-0.793, total=   

[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=-0.539, total=   8.5s
[CV] n_estimators=250, max_depth=50, bootstrap=True ..................
[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=0.702, total=   8.5s
[CV] n_estimators=250, max_depth=50, bootstrap=True ..................
[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=-1.227, total=   8.7s
[CV] n_estimators=250, max_depth=50, bootstrap=True ..................
[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=0.164, total=   8.6s
[CV] n_estimators=250, max_depth=50, bootstrap=True ..................
[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=0.288, total=   8.3s
[CV] n_estimators=250, max_depth=50, bootstrap=True ..................
[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=0.533, total=   8.4s
[CV] n_estimators=250, max_depth=50, bootstrap=True ..................
[CV]  n_estimators=250, max_depth=50, bootstrap=True, score=-1.430, total=   8.1s
[CV]

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed: 17.0min finished


In [31]:

data_submit = pd.DataFrame()

data_submit.loc[:,'Customer Id'] = test_data_ini.loc[:,'Customer Id']
data_submit['Cost'] = Y_predict
data_submit['Cost'] = data_submit['Cost'].abs()

In [33]:
data_submit.to_csv("submission2.csv",index=False)

![](./images/result_submission2.png)

# Final Leaderboard Score

![](./images/leaderboard.png)